In [1]:
import numpy as np
import pandas as pd
import statsmodels.api as sm
import statsmodels.formula.api as smf
from scipy.stats import pearsonr
import matplotlib.pyplot as plt
import seaborn as sb

ModuleNotFoundError: No module named 'statsmodels'

In [ ]:
houses = pd.read_csv("SaratogaHouses_dummies.csv") 

In [ ]:
houses.head()

In [ ]:
Corr_mat = houses.corr()
fig = plt.figure(figsize = (15,15))

sb.heatmap(Corr_mat, vmax = .8, square = True)
plt.show()

In [ ]:
predictors = ['lotSize', 'age', 'landValue', 'livingArea', 
              'pctCollege', 'bedrooms', 'fireplaces', 'bathrooms', 
              'rooms', 'heatingElectric', 'sewerPublic', 
              'waterfront', 'newConstruction', 'centralAir']
outcome = 'price'

In [ ]:
for i in range(len(predictors)):
    for j in range(len(predictors)):
        if i < j:
            corr, _ = pearsonr(houses[predictors[i]], houses[predictors[j]])
            print(f'The correlation between {predictors[i]} and {predictors[j]} is {corr}')

Let's how linearly the predictors correlate with the price

In [ ]:
fig, ax = plt.subplots(3, 3, figsize=[12,10])

for i, axi in enumerate(ax.flat):
    axi.scatter(houses[predictors[i]], houses[outcome], color='tab:orange')
    axi.set_ylabel('Price')
    axi.set_xlabel(f'Predictor: {predictors[i]}')
    axi.set_title("One predictor");

plt.tight_layout()
plt.show()

In [ ]:
model = sm.OLS(houses[outcome], houses[predictors].assign(const=1))
results = model.fit()

In [ ]:
results.summary()

Let's start backwards elimination. The least signigicant predictor is fireplaces -> removed.

In [ ]:
predictors1 = ['lotSize', 'age', 'landValue', 'livingArea', 
              'pctCollege', 'bedrooms', 'bathrooms', 
              'rooms', 'heatingElectric', 'sewerPublic', 
              'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model1 = sm.OLS(houses[outcome], houses[predictors1].assign(const=1))
results1 = model1.fit()

In [ ]:
results1.summary()

Droping fireplaces did not change R^2_adj or the AIC -> dropped fairly. 
The next to be dropped is sewerPublic

In [ ]:
predictors2 = ['lotSize', 'age', 'landValue', 'livingArea', 
              'pctCollege', 'bedrooms', 'bathrooms', 
              'rooms', 'heatingElectric', 'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model2 = sm.OLS(houses[outcome], houses[predictors2].assign(const=1))
results2 = model2.fit()

In [ ]:
results2.summary()

Droping sewerPublic did not change R^2_adj or the AIC -> dropped fairly. The next to be dropped is pctCollege

In [ ]:
predictors3 = ['lotSize', 'age', 'landValue', 'livingArea', 'bedrooms', 'bathrooms', 
              'rooms', 'heatingElectric', 'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model3 = sm.OLS(houses[outcome], houses[predictors3].assign(const=1))
results3 = model3.fit()

In [ ]:
results3.summary()

Droping pctCollege did not change R^2_adj or the AIC -> dropped fairly. heatingElectric is borderline significant. 
Lets dropped and look at how this influences the model.

In [ ]:
predictors4 = ['lotSize', 'age', 'landValue', 'livingArea', 'bedrooms', 'bathrooms', 
              'rooms', 'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model4 = sm.OLS(houses[outcome], houses[predictors4].assign(const=1))
results4 = model4.fit()

In [ ]:
results4.summary()

In [ ]:
predictors5 = ['lotSize', 'age', 'landValue', 'livingArea', 'bedrooms', 'bathrooms', 
              'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model5 = sm.OLS(houses[outcome], houses[predictors5].assign(const=1))
results5 = model5.fit()

In [ ]:
results5.summary()

R^2 dropped a tiny bit but the multicollinearity problems persist. Let's eliminate another dependent predictor.

In [ ]:
predictors6 = ['lotSize', 'age', 'landValue', 'livingArea', 'bathrooms', 
              'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model6 = sm.OLS(houses[outcome], houses[predictors6].assign(const=1))
results6 = model6.fit()

In [ ]:
results6.summary()

R^2 dropped a tiny bit but the multicollinearity problems persist. Let's eliminate another dependent predictor.

In [ ]:
predictors7 = ['lotSize', 'age', 'landValue', 'livingArea', 'waterfront', 'newConstruction', 'centralAir']

In [ ]:
model7 = sm.OLS(houses[outcome], houses[predictors7].assign(const=1))
results7 = model7.fit()

In [ ]:
results7.summary()

R^2 dropped a tiny bit but the multicollinearity problems persist. Let's eliminate another dependent predictor.

In [ ]:
predictors8 = ['lotSize', 'age', 'landValue', 'livingArea', 'waterfront', 'centralAir']

In [ ]:
model8 = sm.OLS(houses[outcome], houses[predictors8].assign(const=1))
results8 = model8.fit()

In [ ]:
results8.summary()

In [ ]:
# For comparison with NN methods let's export the mean squared error of the residuals
mse = results8.mse_resid

In [ ]:
# Roughly here is by how much the house price is mispredicted on average
mse**0.5

In [ ]:
# Here are the parameters of a our final model
results8.params

In [ ]:
# Lets make a prediction
para = results8.params
X = [0.58, 40, 40000, 1980, 1, 1, 1]
prediction = np.dot(para, X)
print(f"This house should cost {prediction}$")